In [1]:
#potrebne klase:

class  cvor:
    def __init__(self, simbol, verovatnoca) -> None:
        self.simbol = simbol
        self.verovatnoca = verovatnoca
        self.kodna_rec = [0] * 20 
        self.ind = 0

class enkodiraniSimbol:
    def __init__(self, simbol, kodna_rec):
        self.simbol = simbol
        self.kodna_rec = kodna_rec

class  cvor_huff:
    def __init__(self, simbol, verovatnoca, levi=None, desni=None) -> None:
        self.simbol = simbol
        self.verovatnoca = verovatnoca
        self.levi = levi
        self.desni = desni
        self.kodna_rec = ''


In [2]:
import math

#izracunavanje entropije binarnog fajla

BR_VREDNOSTI = 256

cf = open("inputFajl1.bin", 'rb')
content = cf.read()

N = len(content)
broj_pojavljivanja = [0] * BR_VREDNOSTI
verovatnoce = [0] * BR_VREDNOSTI

for c in content:           #u ovoj petlji se dobija br pojavljivanja za svaki simbol
    broj_pojavljivanja[c] += 1  

entropija = 0.0

for i in range(BR_VREDNOSTI):
    if broj_pojavljivanja[i] == 0:
        continue

    verovatnoce[i] = 1.0 * broj_pojavljivanja[i] / N 
    #print(f'Izracunavam verovatnocu za {i}, verovatnoca: {verovatnoce[i]:.2f}')
    entropija -= verovatnoce[i] * math.log2(verovatnoce[i])

print(f'Entropija: {entropija:.2f}')

vrednosti = []
for i in range(BR_VREDNOSTI):
    if broj_pojavljivanja[i] > 0:
        vrednosti.append(cvor(chr(i), verovatnoce[i]))
        print(f'Vrednost: {chr(i)} se pojavljuje {broj_pojavljivanja[i]} puta, verovatnoca: {verovatnoce[i]:.2f}.')


Entropija: 2.20
Vrednost: 1 se pojavljuje 461014 puta, verovatnoca: 0.31.
Vrednost: 2 se pojavljuje 346450 puta, verovatnoca: 0.23.
Vrednost: 3 se pojavljuje 346503 puta, verovatnoca: 0.23.
Vrednost: 4 se pojavljuje 230652 puta, verovatnoca: 0.15.
Vrednost: 5 se pojavljuje 115381 puta, verovatnoca: 0.08.


In [3]:
#Shannon Fano kod

import os


def shannon_fano_kodiranje(l, m, vrednosti): 
    deo1 = 0
    deo2 = 0 
    raz1 = 0 
    raz2 = 0

    if (l == m or l > m):
            return 
    if((l + 1) == m) : 
        vrednosti[m].ind+=1
        vrednosti[m].kodna_rec[(vrednosti[m].ind)] = 0
        vrednosti[l].ind+=1
        vrednosti[l].kodna_rec[(vrednosti[l].ind)] = 1
        
        return
    else :
        for i in range(l,m):
            deo1 = deo1 + vrednosti[i].verovatnoca 
        deo2 = deo2 + vrednosti[m].verovatnoca 
        raz1 = abs(deo1 - deo2) 
    
        j = 2
        for j in range(j, m+1): 
            k = m - j 
            deo1 = deo2 = 0 
            for i in range(l, k+1): 
                deo1 = deo1 + vrednosti[i].verovatnoca
            for i in range(m,k,-1): 
                deo2 = deo2 + vrednosti[i].verovatnoca
            raz2 = abs(deo1 - deo2) 
            if (raz2 >= raz1): 
                break
            raz1 = raz2
            
        
        k+=1 
        for i in range(l,k+1):
            vrednosti[i].ind+=1
            vrednosti[i].kodna_rec[(vrednosti[i].ind)] = 1
            
        for i in range(k + 1,m+1):
            vrednosti[i].ind+=1
            vrednosti[i].kodna_rec[(vrednosti[i].ind)] = 0

        shannon_fano_kodiranje(l, k, vrednosti) #rekurzija za levu i desnu stranu dok svakom cvoru ne ostane jedan znak
        shannon_fano_kodiranje(k + 1, m, vrednosti)
       

def stampaj(vrednosti):
    n = len(vrednosti)
    print("\n\n\n\tSimbol\t\tVerovatnoca\tKod",end='')
    for i in range(n - 1,-1,-1):
        print(f'\n\t{vrednosti[i].simbol}\t\t{vrednosti[i].verovatnoca:0.2f}\t\t', end='')
        for j in range(vrednosti[i].ind+1):
            print(vrednosti[i].kodna_rec[j],end='')    

def enkodirajPoruku(inputPoruka, enkodirana):
    for i in inputPoruka:
        for vrednost in vrednosti:
            if vrednost.simbol == i:
                for j in range(vrednost.ind+1):
                    enkodirana += str(vrednost.kodna_rec[j])
                break

    return enkodirana

   
vrednosti.sort(key=lambda x: x.verovatnoca, reverse=False)

for i in range(len(vrednosti)):
        vrednosti[i].ind = -1

shannon_fano_kodiranje(0, len(vrednosti) - 1, vrednosti)

print("---KODIRANJE---")
stampaj(vrednosti)

enkodirana = ""

inputPoruka = content.decode('utf-8')
enkodiranaPoruka = enkodirajPoruku(inputPoruka, enkodirana)

bajtovi = bytearray(int(enkodiranaPoruka[i:i+8], 2) for i in range(0, len(enkodiranaPoruka), 8))
    
with open("kodirana_poruka_ShannonFano.bin", "wb") as f:
    f.write(
        b" ".join(
            f"{vrednost.simbol}:{''.join(str(vrednost.kodna_rec[j]) for j in range(vrednost.ind+1))}".encode("utf-8")
            for vrednost in vrednosti
        ) + b"\n" + bajtovi
    )

def shannon_fano_dekodiranje():
    
    lista_simbola = []  

    with open("kodirana_poruka_ShannonFano.bin", 'rb') as file:
        lista_simbola = [enkodiraniSimbol(vrednost.strip(), kod.strip()) for simbol in file.readline().decode('utf-8').strip().split() if ":" in simbol for vrednost, kod in [simbol.split(":")]]
    
    ostatak = len(enkodiranaPoruka) % 8
    with open("kodirana_poruka_ShannonFano.bin", 'rb') as file:
        file.readline()
        podaci = file.read()

    bitNiz = ''.join(f'{bajt:08b}' for bajt in podaci)
    if ostatak > 0:
        bitNiz = bitNiz[:-8 + ostatak] + bitNiz[-ostatak:]
    
    decodedMsg = ""
    pom = ""
    
    for bit in bitNiz:
        pom += bit
        for simbol in lista_simbola:
            if pom == simbol.kodna_rec:
                decodedMsg += simbol.simbol
                pom = ""
                break  

    return decodedMsg

decodedMsg = shannon_fano_dekodiranje()

with open("inputFajl1.bin", 'rb') as file:
    content = file.read()

with open("dekodirana_poruka_ShannonFano.bin", 'wb') as file:
    file.write(decodedMsg.encode('utf-8'))

with open("dekodirana_poruka_ShannonFano.bin", 'rb') as file:
    contentDecoded = file.read()

if content == contentDecoded:
    print("\n\nUspesno kodiranje i dekodiranje.")
else:
    print("\n\nNeuspesno kodiranje i dekodiranje.") 

inputFileSize = os.path.getsize('inputFajl1.bin')
kompresovaniFileSize = os.path.getsize('kodirana_poruka_ShannonFano.bin')
stepenKompresije = (kompresovaniFileSize / inputFileSize) 

print(f"Stepen kompresije: {stepenKompresije:.2f}")




---KODIRANJE---



	Simbol		Verovatnoca	Kod
	1		0.31		00
	3		0.23		01
	2		0.23		10
	4		0.15		110
	5		0.08		111

Uspesno kodiranje i dekodiranje.
Stepen kompresije: 0.28


In [4]:
#Huffmanov algoritam

import os


def stampajCvorove(cvor, val=''):
     
     novaVrednost = val + str(cvor.kodna_rec) 
  
     if(cvor.levi): 
        stampajCvorove(cvor.levi, novaVrednost) 
     if(cvor.desni): 
        stampajCvorove(cvor.desni, novaVrednost) 
  
     if(not cvor.levi and not cvor.desni): 
        print(f"{cvor.simbol} -> {novaVrednost}") 


def formirajHuffStablo():

    vrednosti_huff = [cvor_huff(vrednosti[i].simbol, vrednosti[i].verovatnoca) for i in range(len(vrednosti))]
    
    while len(vrednosti_huff) > 1: 
  
        vrednosti_huff.sort(key=lambda x: x.verovatnoca, reverse=False)

        levi = vrednosti_huff.pop(0)
        desni = vrednosti_huff.pop(0)
  
        levi.kodna_rec = 0
        desni.kodna_rec = 1
  
        novi = cvor_huff(levi.simbol+desni.simbol, levi.verovatnoca+desni.verovatnoca, levi, desni) 
  
        vrednosti_huff.append(novi)
    return vrednosti_huff[0]

 
def enkodirajPoruku(inputNiz, root):
    kodiranNiz = ""

    for kod in inputNiz:
        kodiranNiz += vratiKodnuRec(root, kod)

    return kodiranNiz


def vratiKodnuRec(root, simbol, trenutni_kod=""):
    if not root:
        return None

    if root.simbol == simbol:
        return trenutni_kod
    else:
        levi_kod = vratiKodnuRec(root.levi, simbol, trenutni_kod + "0")
        desni_kod = vratiKodnuRec(root.desni, simbol, trenutni_kod + "1")

        if levi_kod:
            return levi_kod
        elif desni_kod:
            return desni_kod


def upisiCvorove(cvor, vrednost=''):
    novaVrednost = vrednost + str(cvor.kodna_rec)
    
    upis = ""

    if cvor.levi:
        upis += upisiCvorove(cvor.levi, novaVrednost)
    if cvor.desni:
        upis += upisiCvorove(cvor.desni, novaVrednost)

    if not cvor.levi and not cvor.desni:
        upis += f"{cvor.simbol}:{novaVrednost} "

    return upis

def dekodiraj_Huff(bitNiz, listaSimbola):

    decodedMsg = ""
    pom = ""
    
    for bit in bitNiz:
        pom += bit
        for simbol in listaSimbola:
            if pom == simbol.kodna_rec:
                decodedMsg += simbol.simbol
                pom = ""
                break  

    return decodedMsg

def ucitajKodove():

    lista_simbola = [] 

    with open("kodirana_poruka_Huffman.bin", 'rb') as file:
        ucitano = file.readline().decode('utf-8').strip().split()

        for vrednost, kod in (ucitan.split(":") for ucitan in ucitano):
            lista_simbola.append(enkodiraniSimbol(vrednost, kod))


    return lista_simbola

def ucitajPoruku():

    ostatak  = duzinaHuff % 8

    with open("kodirana_poruka_Huffman.bin", 'rb') as file:
        file.readline()
        podaci = file.read()

    bitNiz = []
    for bajt in podaci:
        bitNiz.extend(map(int, bin(bajt)[2:].rjust(8, '0')))
   
    bitNiz = ''.join(map(str, bitNiz))

    if ostatak > 0:
        bitNiz = bitNiz[:-8] + bitNiz[-8:][8 - ostatak:]

    return bitNiz


root_huff = formirajHuffStablo()
print("---KODIRANJE---\n")
stampajCvorove(root_huff) 

enkodiranaPoruka = enkodirajPoruku(content.decode('utf-8'), root_huff)
duzinaHuff = len(enkodiranaPoruka)

bajtovi = bytearray(int(enkodiranaPoruka[i:i+8], 2) for i in range(0, len(enkodiranaPoruka), 8))

with open("kodirana_poruka_Huffman.bin", "wb") as fajl:
    fajl.write(upisiCvorove(root_huff).encode("utf-8") + b"\n" + bajtovi)


listaSimbola = ucitajKodove()
bitNiz = ucitajPoruku()
decodedMsg = dekodiraj_Huff(bitNiz, listaSimbola)

with open("inputFajl1.bin", 'rb') as file:
    content = file.read()

with open("dekodirana_poruka_Huffman.bin", 'wb') as file:
    file.write(decodedMsg.encode('utf-8'))

with open("dekodirana_poruka_Huffman.bin", 'rb') as file:
    contentDecoded = file.read()


if content == contentDecoded:
    print("\nUspesno kodiranje i dekodiranje.")
else:
    print("\nNeuspesno kodiranje i dekodiranje.") 

inputFileSize = os.path.getsize('inputFajl1.bin')
kompresovaniFileSize = os.path.getsize('kodirana_poruka_Huffman.bin')
stepenKompresije = (kompresovaniFileSize / inputFileSize) 

print(f"Stepen kompresije: {stepenKompresije:.2f}") 


---KODIRANJE---

5 -> 000
4 -> 001
2 -> 01
3 -> 10
1 -> 11

Uspesno kodiranje i dekodiranje.
Stepen kompresije: 0.28


In [14]:
#lzw algoritam

simboli = []
def lzw_kodiranje(inputPoruka):
    
    global simboli
    simboli = list(set(inputPoruka))
    
    recnik = {simboli[i]: i for i in range(len(simboli))}

    p = ""
    c = ""
    p += inputPoruka[0]
    kodna_rec = len(recnik)
    enkodiranaPoruka = []

    print("----RECNIK----\n")
    print("Simbol:\tKod:\t\tNovi simboli:")
    for i in range(len(inputPoruka)):
        if i != len(inputPoruka) - 1:
            c += inputPoruka[i + 1]
        if p + c in recnik:
            p = p + c
        else:
            print(f"{p}\t{recnik[p]}\t\t{p + c}\t{kodna_rec}")
            enkodiranaPoruka.append(recnik[p])
            recnik[p + c] = kodna_rec
            kodna_rec += 1
            p = c
        c = ""

    print(f"{p}\t{recnik[p]}")
    enkodiranaPoruka.append(recnik[p])
    
    binarnaPoruka = ''.join(format(kod, '08b') for kod in enkodiranaPoruka)
    
    bajtovi = bytearray(int(binarnaPoruka[i:i+8], 2) for i in range(0, len(binarnaPoruka), 8))

    
    with open("kodirana_poruka_LZW.bin", "wb") as f:
  
        f.write(bajtovi)
    
    return enkodiranaPoruka

def lzw_dekodiranje(enkodirana):
   
    recnik = {i: simboli[i] for i in range(len(simboli))}
    dekodiranaPoruka = []

    preth = enkodirana[0]
    s = recnik[preth]
    c = ""
    c += s[0]
    print(s, end="")
    dekodiranaPoruka.append(s)

    count = len(recnik)

    for i in range(len(enkodirana) - 1):
        temp = enkodirana[i + 1]
        if temp not in recnik:
            s = recnik[preth]
            s = s + c
        else:
            s = recnik[temp]
        dekodiranaPoruka.append(s)
        c = ""
        c += s[0]
        recnik[count] = recnik[preth] + c
        count += 1
        preth = temp

    return ''.join(dekodiranaPoruka)

cf = open("inputFajl2.bin", 'rb')
content = cf.read()
inputPoruka = content.decode('utf-8')
enkodiranaPoruka = lzw_kodiranje(inputPoruka)

dekodiranaPoruka = lzw_dekodiranje(enkodiranaPoruka)

if inputPoruka == dekodiranaPoruka:
    print("\n\nUspesno kodiranje i dekodiranje.")
else:
    print("\n\nNeuspesno kodiranje i dekodiranje.")


inputFileSize = os.path.getsize('inputFajl2.bin')
kompresovaniFileSize = os.path.getsize('kodirana_poruka_LZW.bin')
stepenKompresije = (kompresovaniFileSize / inputFileSize) 

print(f"Stepen kompresije: {stepenKompresije:.2f}")

----RECNIK----

Simbol:	Kod:		Novi simboli:
B	0		BA	3
A	2		AA	4
A	2		AC	5
C	1		CB	6
B	0		BB	7
BB	7		BBA	8
AA	4		AAA	9
AC	5		ACB	10
BA	3		BAB	11
BBA	8		BBAC	12
C	1		CA	13
AA	4		AAB	14
BA	3		BAA	15
AAA	9		AAAA	16
AAB	14		AABA	17
A	2		AB	18
B	0		BC	19
CA	13		CAB	20
BAA	15		BAAA	21
ACB	10		ACBB	22
BAA	15		BAAB	23
BB	7		BBB	24
BB	7		BBC	25
CB	6		CBA	26
AC	5		ACA	27
AB	18		ABB	28
BBB	24		BBBC	29
CB	6		CBC	30
C	1		CC	31
CBA	26		CBAA	32
AB	18		ABA	33
ACBB	22		ACBBB	34
BBB	24		BBBB	35
BBC	25		BBCA	36
ABB	28		ABBA	37
ACBB	22		ACBBC	38
CAB	20		CABB	39
BBBB	35		BBBBB	40
BAAA	21		BAAAA	41
ABA	33		ABAA	42
AB	18		ABC	43
CA	13		CAA	44
ACA	27		ACAC	45
CBC	30		CBCB	46
BBBBB	40		BBBBBA	47
AAA	9		AAAB	48
BC	19		BCA	49
AC	5		ACC	50
CA	13		CAC	51
CBAA	32		CBAAB	52
BBB	24		BBBA	53
AAAA	16		AAAAA	54
ABB	28		ABBB	55
BAB	11		BABA	56
ACB	10		ACBC	57
CAA	44		CAAB	58
BAB	11		BABB	59
BAB	11		BABC	60
CC	31		CCA	61
ABBA	37		ABBAC	62
CBCB	46		CBCBB	63
BCA	49		BCAB	64
BBA	8		BBAA	65
ABC	43		ABCC	66
CB	6		CBB	67
BC	19		

In [15]:
#lz77


import struct
import math

def lz77_pretrazi(searchBuffer, lookaheadBuffer):
    sb_len = len(searchBuffer) #search buffer len
    lb_len = len(lookaheadBuffer)    #lookahead buffer len

    if sb_len == 0:
        return (0, 0, lookaheadBuffer[0])

    if lb_len == 0:
        return (-1, -1, "")

    najbolja_duzina = 0
    najbolji_ind = 0
    bafer = searchBuffer + lookaheadBuffer

    searchPointer = sb_len
    for i in range(0, sb_len):
        duzina = 0
        while bafer[i + duzina] == bafer[searchPointer + duzina]:
            duzina += 1
            if searchPointer + duzina == len(bafer):
                duzina -= 1
                break
            if i + duzina >= searchPointer:
                break
        if duzina > najbolja_duzina:
            najbolji_ind = i
            najbolja_duzina = duzina

    return (najbolji_ind, najbolja_duzina, bafer[searchPointer + najbolja_duzina])

def lz77_kodiranje(inputPoruka, prozor_len):
    lb_maxLen = int(math.pow(2, (16 - (math.log(prozor_len, 2)))))
    kodiranaPoruka = []
    searchPointer = 0
    lookaheadPointer = 0

    while lookaheadPointer < len(inputPoruka):
        searchBuffer = inputPoruka[searchPointer:lookaheadPointer]
        lookaheadBuffer = inputPoruka[lookaheadPointer:lookaheadPointer + lb_maxLen]
        (ind, duzina, znak) = lz77_pretrazi(searchBuffer, lookaheadBuffer)
        kodiranaPoruka.append((ind, duzina, znak))

        lookaheadPointer += duzina + 1
        searchPointer = lookaheadPointer - prozor_len
        if searchPointer < 0:
            searchPointer = 0

    return kodiranaPoruka

def sacuvaj_kodirano(kodiranaPoruka, izlaznaDatoteka):
    with open(izlaznaDatoteka, "wb") as file:
        for (ind, duzina, znak) in kodiranaPoruka:
            indShift = ind << 6
            duzina_ind = indShift + duzina
            bajtovi = struct.pack(">Hc", duzina_ind, znak.encode('latin1'))
            file.write(bajtovi)


prozor_len = 256

def lz77_dekodiranje(kodiranaPoruka, prozor_len):
    chararray = ""
    i = 0

    while i < len(kodiranaPoruka):
        (offset_and_length, char) = struct.unpack(">Hc", kodiranaPoruka[i:i + 3])
        ind = offset_and_length >> 6
        length = offset_and_length - (ind << 6)
        i += 3

        if ind == 0 and length == 0:
            chararray += char.decode('latin1')
        else:
            iterator = len(chararray) - prozor_len
            if iterator < 0:
                iterator = ind
            else:
                iterator += ind
            for pointer in range(length):
                chararray += chararray[iterator + pointer]
            chararray += char.decode('latin1')

    return chararray

inputPoruka = content.decode('utf-8')
kodiranaPoruka = lz77_kodiranje(inputPoruka, prozor_len)

sacuvaj_kodirano(kodiranaPoruka, "kodirana_poruka_LZ77.bin")

with open("kodirana_poruka_LZ77.bin", 'rb') as file:
        ucitanaKodiranaPoruka = file.read()

dekodiranaPoruka = lz77_dekodiranje(ucitanaKodiranaPoruka, prozor_len)
print("----IZLAZ----\n")
print("[indeks, duzina, znak]")
for (ind, duzina, znak) in kodiranaPoruka:
    print(f"[ {ind}, {duzina}, {znak} ]")
'''
print("\nDekodirana poruka:")
print(dekodiranaPoruka)
'''
if inputPoruka == dekodiranaPoruka:
    print("\n\nUspesno kodiranje i dekodiranje.")
else:
    print("\n\nNeuspesno kodiranje i dekodiranje.")

inputFileSize = os.path.getsize('inputFajl2.bin')
kompresovaniFileSize = os.path.getsize('kodirana_poruka_LZ77.bin')
stepenKompresije = (kompresovaniFileSize / inputFileSize) 

print(f"Stepen kompresije: {stepenKompresije:.2f}")


----IZLAZ----

[indeks, duzina, znak]
[ 0, 0, B ]
[ 0, 0, A ]
[ 1, 1, C ]
[ 0, 1, B ]
[ 0, 3, A ]
[ 3, 2, A ]
[ 5, 3, C ]
[ 1, 2, B ]
[ 7, 3, A ]
[ 17, 4, B ]
[ 16, 2, B ]
[ 7, 5, B ]
[ 17, 3, B ]
[ 4, 2, C ]
[ 14, 4, B ]
[ 41, 5, C ]
[ 10, 3, A ]
[ 14, 3, B ]
[ 40, 4, B ]
[ 28, 4, B ]
[ 2, 4, C ]
[ 39, 5, B ]
[ 19, 5, B ]
[ 17, 3, C ]
[ 1, 3, A ]
[ 53, 3, B ]
[ 82, 7, B ]
[ 97, 3, C ]
[ 9, 4, A ]
[ 83, 7, A ]
[ 4, 4, B ]
[ 98, 4, A ]
[ 25, 4, B ]
[ 27, 3, C ]
[ 71, 6, C ]
[ 68, 7, A ]
[ 54, 4, B ]
[ 134, 6, B ]
[ 90, 6, C ]
[ 54, 3, C ]
[ 130, 4, B ]
[ 145, 4, A ]
[ 13, 4, C ]
[ 75, 4, C ]
[ 112, 4, B ]
[ 11, 5, A ]
[ 7, 4, A ]
[ 198, 5, A ]
[ 27, 3, B ]
[ 131, 6, B ]
[ 51, 5, B ]
[ 1, 3, C ]
[ 18, 5, B ]
[ 46, 5, A ]
[ 85, 6, C ]
[ 49, 5, A ]
[ 40, 7, A ]
[ 114, 4, C ]
[ 251, 5, A ]
[ 9, 4, C ]
[ 72, 3, A ]
[ 182, 6, B ]
[ 87, 4, B ]
[ 90, 9, B ]
[ 93, 5, C ]
[ 23, 5, B ]
[ 130, 5, C ]
[ 27, 6, C ]
[ 161, 4, A ]
[ 85, 5, A ]
[ 229, 6, C ]
[ 66, 4, B ]
[ 37, 4, A ]
[ 225, 6, B ]
[ 156